### Theoretical definitions

#### Multi armed bandit problem:

In this part of my answer I will firstly describe multi armed bandit problem, and then I will mention about main struggles of solving the problem and common solutions.

Multi armed bandit problem is a problem which generated to work on maximize expected gain with limited resources when you work with uncertain probability of success. To make that problem more realistic and understandable for everyone a scenario is created. In scenario, there are row of slot machines and you have limited number of coins or time to play with that machines. Your main purpose is maximizing your gains. However. you don’t know about win rate of slot machines.

So. At first step we need to explore win rate of slot machines when we try to maximize our gains. This situation called as a explore-exploit dilemma. <ins>Thomson Sampling</ins> is one of the most common way to solve this problem. I will detailly describe <ins>Thomson Sampling</ins> beyond. 

Next problem is defining win rate of slot machines. In this point we will have to create a data set. In order to create that dataset, we will benefit from <ins>Beta Bernoulli Model</ins>. 

However even after we create dataset, we cannot be sure about win rate of slot machines. So, need to define winning rate for every slot machine. Directly defining winning rate as maximum likelihood will not cover uncertainty.  To solve this problem, we will benefit from <ins>Bayesian inference</ins> to define winning posterior distribution for each slot machine.

#### Thomson Sampling

As we mentioned above Thomson sampling is one of the most popular solution in order to solve explore-exploit dilemma. This algorithm evaluates our current situation and historical data and as an end product gives us next slot to play with. Thomson Sampling follows strategy which is called as probability matching.
•	At each round, we calculate the posterior distribution of θk, for each of the K bandits.
•	We draw a single sample of each of our θk and pick the one with the largest value.
#### Beta Bernoulli Model:
	
Bernoulli Model is special binomial distribution just with one sample 
”binomial(1, θk)”. To create data set we benefit from Bernoulli Model. Bernuolli model generate random variable [0,1] with success probability of θk. After we took result from our prior distribution to create our posterior distribution, we benefit from Beta distribution. 


#### Bayesian Approach:

The methods I mentioned above which are generating posterior distribution is called as Bayesian Approach. We benefit from this approach to have useful information about slot machines winning rate distribution. 


In [1]:
%matplotlib inline
import warnings
warnings.filterwarnings('ignore')
import numpy as np
import matplotlib.pyplot as plt
import seaborn as sns
from scipy.stats import beta as beta_dist
from matplotlib.animation import FuncAnimation
from IPython.display import HTML
from tqdm import tqdm
from modules import decisionmethods
from modules import simulation
from modules.helper.helper import regret_visualization
from modules.helper.helper import beta_pdf
from modules.helper.helper import prob_visualization
import pickle
import os
plt.ioff()
plt.style.use('fivethirtyeight')

In [2]:
# Define slot probailities and number of tome which will be simulate
number_play =  500
slot_probabilities = [0.1, 0.4, 0.45, 0.6, 0.61]
decision_method = decisionmethods.DecisionMethods()

In [3]:
# Random Sampling method 
random_sample_simulation = simulation.Simulation(decision_method=decision_method.random_sampling, 
                                                 number_play=number_play,slot_probabilities=slot_probabilities)
# Thomson Sampling method 
thomson_sampling_simulation = simulation.Simulation(decision_method=decision_method.thomson_sampling, 
                                                 number_play=number_play,slot_probabilities=slot_probabilities)
# e-greedy Sampling method 
e_greedy_sample_simulation = simulation.Simulation(decision_method=decision_method.e_greedy_sampling, 
                                                 number_play=number_play,slot_probabilities=slot_probabilities)

#UCB Sampling Method
UCB_sample_simulation = simulation.Simulation(decision_method=decision_method.upper_confidence_bounce_sampling, 
                                                 number_play=number_play,slot_probabilities=slot_probabilities)

#customized Thomson Sampling discover Method
customized_thomson_sampling_discover_simulation = simulation.Simulation(decision_method=decision_method.customized_thomson_sampling_discover, 
                                                 number_play=number_play,slot_probabilities=slot_probabilities)

#customized Thomson Sampling uncertanity Method
customized_thomson_sampling_uncertanity_simulation = simulation.Simulation(decision_method=decision_method.customized_thomson_sampling_discover, 
                                                 number_play=number_play,slot_probabilities=slot_probabilities)




In [4]:
#Simulate multi armed bandit problem with different sampling methods
random_sample_simulation.bayesian_simulation()
thomson_sampling_simulation.bayesian_simulation()
e_greedy_sample_simulation.bayesian_simulation()
UCB_sample_simulation.bayesian_simulation()
customized_thomson_sampling_discover_simulation.bayesian_simulation()
customized_thomson_sampling_uncertanity_simulation.bayesian_simulation()


In [ ]:
# Create animation for every sampling method
anim_random = random_sample_simulation.animation(plot_title='Random sampling simulation')
anim_thomson = thomson_sampling_simulation.animation(plot_title='Thomson sampling simulation')
anim_e_greedy = e_greedy_sample_simulation.animation(plot_title='e-greedy sampling simulation')
anim_UCB = UCB_sample_simulation.animation(plot_title='UCB sampling simulation')
anim_TS_discover = customized_thomson_sampling_discover_simulation.animation(plot_title='TS discover simulation')
anim_TS_uncertanity = customized_thomson_sampling_uncertanity_simulation.animation(plot_title='TS uncertanity simulation')

In [6]:
anim_list = [anim_random, anim_thomson, anim_e_greedy, anim_UCB, anim_TS_discover, anim_TS_uncertanity]
file_list = ['random', 'thomson', 'e_greedy', 'UCB', 'TS_discover', 'TS_Uncertainty']
path = 'animations'
video_list = []

#### <span style="color:red">  Cauntion </span>
Code below is rendering animation to video. So it takes too long to complete. If you want to render videos again you can delete # before codes. However videos already rendered and added to project you can just call animations too. 

In [7]:
# for file, anim in zip(file_list,anim_list):
#     video = anim.to_html5_video()
#     filename = os.path.join(path, file)
#     outfile = open(filename,'wb')
#     pickle.dump(video,outfile)
#     outfile.close()

In [8]:
for file, anim in zip(file_list,anim_list):
    filename = os.path.join(path, file)
    infile = open(filename,'rb')
    video_list.append(pickle.load(infile))
    infile.close()

I animated both squence of decision and posterior distribution. So you can observe evolution of posterior distributon and estimation of best slot. 

Clearly when the number of play increase standart deviation is deacreasing as expected

I created two different new algorithm <ins>TS discover</ins> and <ins>TS uncertanity</ins>

###### <ins>TS discover:</ins>  
In this algorithm I added epsilon random threshold to algoritm. As I observe after a while Thomson Sampling begin to just focus on one option because of higher probability of winning. I expected epsilon to let it help to discover other slots. Didn't work well because in this condition learn rate decreased in long term. Also our number of slots are very low and also stable so we don@t need to discover.

###### <ins>TS uncertainty:</ins>  
In this algorithm I tried to solve uncertanity problem and created a algorithm which generate value from beta distribution 10 times. Then use average of them to decide which slot is better option. Thanks to this method many time TS uncertainity algoritym worked better than Thomson Sampling. However still randomness can change the results. 

In [9]:
HTML(video_list[0])

In [10]:
HTML(video_list[1])

In [11]:
HTML(video_list[2])

In [12]:
HTML(video_list[3])

In [13]:
HTML(video_list[4])

In [14]:
HTML(video_list[5])

#### The evolution of regret over time.

In [15]:
regret_visualization(random_method=random_sample_simulation.regret_cum_list,
                     thomson_method=thomson_sampling_simulation.regret_cum_list,
                     e_greedy_method=e_greedy_sample_simulation.regret_cum_list,
                     upper_confidence_bounce_sampling=UCB_sample_simulation.regret_cum_list,
                     thomson_method_discover=customized_thomson_sampling_discover_simulation.regret_cum_list,
                     thomson_method_uncertainty=customized_thomson_sampling_uncertanity_simulation.regret_cum_list)

##### Prediction of probabilities
As you can see below generally every algorithms have accuret prediction on succes probability of slot machines. Generally algorithms except random is not too succesfull when they predict success probability of slot number 1,2 and 3. Generally tried to stay away from low probability so number of instange is too low to have better prediction on slot number 1,2 and 3. 

In [16]:
prob_visualization(random_method=random_sample_simulation,
                     thomson_method=thomson_sampling_simulation,
                     e_greedy_method=e_greedy_sample_simulation,
                     upper_confidence_bounce_sampling=UCB_sample_simulation,
                     thomson_method_discover=customized_thomson_sampling_discover_simulation,
                     thomson_method_uncertainty=customized_thomson_sampling_uncertanity_simulation)